## Reproducibility in different acquisition settings - Statistics

### Reproducibility metrics analysis

In [1]:
suppressWarnings(suppressMessages(library("car")))
suppressWarnings(suppressMessages(library("sjstats")))
suppressWarnings(suppressMessages(library("broom")))
suppressWarnings(suppressMessages(library("multcomp")))

library("car")
library("broom")
library("multcomp")
library("sjstats")
library("xtable")

path_resources <- file.path(getwd(), "..", "..", "resources", "data")

path_col <- file.path(path_resources, "r2_repository_and_site_adult_a2009s.csv")
data_col <- read.csv(path_col)
data_col$repository_and_site <- as.factor(data_col$repository_and_site)

map_aov <- list("r_square"=aov(r_square ~ repository_and_site + age + snr_total, data = data_col), 
                "ICC"=aov(ICC ~ repository_and_site + age + snr_total, data = data_col))


for (rep_measure in c("r_square", "ICC")){
  
  print(sprintf("## #####################      %s      ################################", rep_measure))  
  
  my_anova <- map_aov[[rep_measure]]
  print(Anova(my_anova, type = "III"))
  pos_hoc <- summary(glht(my_anova, linfct = mcp(repository_and_site="Tukey")))
    
  latex_table_name = sprintf("adult_a2009s_%s_first_level.txt", rep_measure)
  latex_table_name_posthoc = sprintf("adult_a2009s_%s_first_level_posthoc.txt", rep_measure)
  df = anova_stats(my_anova)[, c("df", "sumsq", "statistic", "p.value", "cohens.f")]
  print(xtable(df, caption = sprintf("adult III %s", rep_measure)), file=latex_table_name)
  print(pos_hoc)
}

[1] "## #####################      r_square      ################################"
Anova Table (Type III tests)

Response: r_square
                    Sum Sq   Df  F value    Pr(>F)    
(Intercept)         0.4743    1  86.8504 < 2.2e-16 ***
repository_and_site 5.6296    3 343.6292 < 2.2e-16 ***
age                 0.0074    1   1.3638    0.2431    
snr_total           0.2305    1  42.2002 1.273e-10 ***
Residuals           5.6958 1043                       
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

	 Simultaneous Tests for General Linear Hypotheses

Multiple Comparisons of Means: Tukey Contrasts


Fit: aov(formula = r_square ~ repository_and_site + age + snr_total, 
    data = data_col)

Linear Hypotheses:
                         Estimate Std. Error t value Pr(>|t|)    
IXI|HH - IXI|Guys == 0  -0.075537   0.008529  -8.857  < 1e-04 ***
IXI|IOP - IXI|Guys == 0 -0.346548   0.011046 -31.372  < 1e-04 ***
OASIS3 - IXI|Guys == 0   0.062017   0.015593   3.977 0.00032

### Analysis of age effect on reproducibility metrics

In [2]:
sites <- c("IXI|Guys", "IXI|HH", "IXI|IOP", "OASIS3")
site_combinations <- combn(sites, 2)


for (rep_measure in c("r_square", "ICC")){

  print(sprintf("#######################      %s      ################################", rep_measure))  
  equation = sprintf("%s ~ age  + snr_total", rep_measure)
  
  var_name = "age"
  
  t_values_list <- c()
  p_values_list <- c()
  cohen_d_list <- c()
  comb_list <- c()
  
  for (i in c(1, 2, 3, 4)){
      
    site1 = site_combinations[1, i]
    site2 = site_combinations[2, i]
    
    n1 =  sum(data_col$repository_and_site == site1)
    n2 = sum(data_col$repository_and_site == site2)
    
    degrees_freedom = n1+n1-2
    
    lmsite1 <- lm(data=data_col, equation, subset = repository_and_site==site1)
    lmsite2 <- lm(data=data_col, equation, subset = repository_and_site==site2)
      
              
      for (var_name in c("age")){

          degrees_freedom = n1+n1-2

          m1 = summary(lmsite1)[["coefficients"]][var_name,"Estimate"]
          m2 = summary(lmsite2)[["coefficients"]][var_name,"Estimate"]

          s1 =  summary(lmsite1)[["coefficients"]][var_name, "Std. Error"] 
          s2 =  summary(lmsite2)[["coefficients"]][var_name, "Std. Error"] 
          

          mean_diff = m1 - m2

          sp = (((n1-1)*(s1**2) + (n2-1)*(s2**2))/(n1+n2-2))**0.5
          cohen_d <- mean_diff/sp

          dem_samples = (1/n1+1/n2)**0.5
          t = mean_diff/(sp*dem_samples)

          p_value <- pt(-abs(t),degrees_freedom)

          t_critical_value <- qt(1-.05/2, degrees_freedom)

          #print(sprintf("\n----------- %s  Slope: Independent t-test -----------\n", var_name))
          #print(sprintf("%s-%s", site1, site2))
          print(sprintf("%s-%s,ndegree,%d,diff,%f,t-value,%f,t-critical-value,%f,p-value,%e,cohen_d,%f", site1, site2, n1+n2-2, mean_diff, t, t_critical_value, p_value*4, cohen_d))
          #cat("Cohen's d effect %d", cohen_d)
          }
  }
  df <- data.frame("combination" = comb_list, "t" = t_values_list, "p-values" = p_values_list, "cohen-d" = cohen_d_list)
  print(df)

for (site_name in sites){
  lm_model <- lm(data=data_col, equation, subset = repository_and_site==site_name)
  #print(sprintf("------ %s ------", site_name))
  print(summary(lm_model))
}
}


[1] "#######################      r_square      ################################"
[1] "IXI|Guys-IXI|HH,ndegree,489,diff,-0.000526,t-value,-18.621937,t-critical-value,1.963785,p-value,1.517107e-61,cohen_d,-1.746071"
[1] "IXI|Guys-IXI|IOP,ndegree,377,diff,-0.000474,t-value,-9.608958,t-critical-value,1.963785,p-value,3.560140e-20,cohen_d,-1.293842"
[1] "IXI|Guys-OASIS3,ndegree,801,diff,-0.001824,t-value,-72.635786,t-critical-value,1.963785,p-value,1.024756e-305,cohen_d,-5.258845"
[1] "IXI|HH-IXI|IOP,ndegree,244,diff,0.000052,t-value,0.704264,t-critical-value,1.966650,p-value,9.634575e-01,cohen_d,0.100865"
data frame with 0 columns and 0 rows

Call:
lm(formula = equation, data = data_col, subset = repository_and_site == 
    site_name)

Residuals:
     Min       1Q   Median       3Q      Max 
-0.30187 -0.03016  0.00730  0.03737  0.13859 

Coefficients:
              Estimate Std. Error t value Pr(>|t|)    
(Intercept)  0.6853462  0.0618708  11.077  < 2e-16 ***
age         -0.0008522  0.000